### Problem Statement: Develop a 3gram & a 2gram LM using Laplace smoothing without using nltk and spacy

#### Training Data: English news Corpus (2020 year) containing around 10,000 sentences.

### Importing Libraries



In [1]:
#importing necessary libraries
from collections import defaultdict
import numpy as np
import random
import string
import copy
import re

### Necessary Preprocessing Data Function

In [2]:
# Function to read the data from given file
def read_text_data_from_file(file_path):
    raw_data = open(file_path, encoding="utf8").read().split("\n")
    
    return raw_data

#### Split Training and Test data :
This function randomly shuffles the given data and splits the data into training and test data based on the specified training size. 


In [3]:
def split_data_into_train_test(raw_data, training_size):

    random.shuffle(raw_data)
    train_data = raw_data[:int((len(raw_data)+1)*training_size)] 
    test_data = raw_data[int((len(raw_data)+1)*training_size):] 
    
    return train_data, test_data

## Preprocessing the data
Preprocessing the model will involve the following steps:

1.Performing regular expression-based substitution for alphanumeric characters,URL,https etc. in the text variablle .

2.Replace the Contractions

3.Lowercasing

4.Removing Punctuation

In the cleaning process, we refrain from removing any stop words or performing lemmatization. Our intention is to preserve the natural flow of the sentence, as such actions can alter the intended meaning and impact the overall coherence. Furthermore, during sentence generation, these measures would not contribute significantly to the sense conveyed.

In [4]:
def preprocessing_cleaning_data(raw_data):
    
    cleaned_data = []

    #dictionary consisting of the contraction and the actual value
    Apos_dict={"'s":" is","n't":" not","'m":" am","'ll":" will", "'d":" would","'ve":" have","'re":" are"}

    for data in raw_data:

        if data == "": continue
            
        #Performing regular expression-based substitution for alphanumeric characters,URL,https etc. in the text variablle  
        
        text = data.split("\t")[1]
        text = re.sub(r"(@\[A-Za-z0-9]+)|([^0-9A-Za-z \t])|(\w+:\/\/\S+)|^rt|http.+?", "", text)

        #replace the contractions
        for key,value in Apos_dict.items():
            if key in text:
                text = text.replace(key,value)

        clean_text = ""
        #remove punctuations
        for word in text.split():
            if word not in string.punctuation:
                clean_text += word + " "
        #Lowercasing 
        clean_text = clean_text.lower()
        clean_text = re.sub(' +', ' ', clean_text)
        clean_text = clean_text.strip()

        cleaned_data.append(clean_text)
        
    return cleaned_data       

## Language Model Function
An N-gram model is one type of a Language Model (LM), which is about finding the probability distribution over word sequences. Given a sequence of N-1 words, an N-gram model predicts the most probable word that might follow this sequence. It's a probabilistic model that's trained on a corpus of text.
A model that simply relies on how often a word occurs without looking at previous words is called unigram. If a model considers only the previous word to predict the current word, then it's called bigram. If two previous words are considered, then it's a trigram model.






In [5]:
'''
Function for generating n-grams from the sentence in 
Parameters:
    sentences: sentences from training data,
    N - value for n-gram ,if it's bigram or trigram
    token_start_word: start token
    token_end_word: end token
'''

def create_ngrams(sentences, N, token_start_word, token_end_word):
    
    grams = []
    for sentence in sentences:
        for i in range(1,N):
                sentence = token_start_word + " " + sentence 
                sentence = sentence + " " + token_end_word

        sentence = sentence.split()

        for i in range(len(sentence) - N + 1):
            grams.append(sentence[i: i + N])
    
    return grams

In [6]:
'''
Function to build the language model from the training data using laplace technique
Parameters:
    grams:input returned from create_ngram() 
    number_unique_words: number of unique words in training data
    laplace value
'''
def create_lm_model(grams, number_unique_words, laplace_value):
    
    lm_prob = defaultdict(lambda: defaultdict(lambda: 0.0))

    for grams_i in grams:

        lm_prob[tuple(grams_i[:-1])][grams_i[-1]] += 1

    # Convert counts to probabilities and apply Laplace smoothing.
    for prev_words in lm_prob:
        total_count = (float(sum(lm_prob[prev_words].values())))
        total_count += number_unique_words

        for current_word in lm_prob[prev_words]:
            lm_prob[prev_words][current_word] += laplace_value
            lm_prob[prev_words][current_word] /= (total_count)

    
    return lm_prob
        

### Implement Sentence Generation 
sentence generation for Language Model. Start by generating the \<s> token, then sampling from the n-grams begining with \<s>. Stop generating words when you hit an \</s> token.

In [7]:
# function to generate random sentences
def generate_random_sentences(text_data, number_of_time_sentence_generate,N):
    
    N = N-1
    generated_sentences = []
    
    for i in range(0, number_of_time_sentence_generate):
        text = copy.deepcopy(text_data)

        sentence_generation_complete = False

        prob = -1
        while not sentence_generation_complete:
 
            r = random.random()
            accumulator = .0

            for word in lm_prob[tuple(text[-N:])].keys():
                accumulator += lm_prob[tuple(text[-N:])][word]
                # select words that are above the probability threshold
                if accumulator >= r:

                    if prob == -1:
                        prob = lm_prob[tuple(text[-N:])][word]
                    else:
                        prob *= lm_prob[tuple(text[-N:])][word]
                    text.append(word)

                    break

            if text[-1:] == ["</s>"]:
                sentence_generation_complete = True

        sent =  (' '.join([t for t in text if t]), (prob))
        generated_sentences.append(sent)
        
    return generated_sentences

In [8]:
# function to get list of unique words, number of unique words, unigram frequency
def get_unique_words_count(sentences):

    unigrams_freq = {}
    unique_words = set()

    for i in sentences:
        for j in i.split():
            unique_words.add(j)
            
            if j in unigrams_freq.keys():
                unigrams_freq[j] += 1
            else:
                unigrams_freq[j] = 1

    return list(unique_words), len(unique_words), unigrams_freq

In [9]:
# function to get the probability of sentence
def get_sentence_prob(sentence, N, token_start_word, token_end_word, lm_prob):

    grams = create_ngrams([sentence], N, token_start_word, token_end_word)
    total_prob = -1
    for grams_i in grams:

        p = lm_prob[tuple(grams_i[:-1])][grams_i[-1]]
        
        if p == 0:
            print("Warning, input sentence contains OOV, and might not use from the training corpus.")
            
        if total_prob == -1:
            total_prob = np.log(p) 
        else:
            total_prob += np.log(p)
    
    return total_prob

In [10]:
# fucntion to get word count in given corpus
def get_word_count_in_corpus(sentences):
    c = 0
    for i in sentences:
        for j in i.split():
            c += 1
    return c

In [11]:
'''
Function to handle unknown words and perform laplace smoothing 
Returns the sentence probalility ,variance and perplexity of sentence.
'''

def get_perplexity_variance(sentences, N, token_start_word, token_end_word, log_probs, laplace_value, number_unique_words):
    
    log_probs = 0
    count_oov = 0
    probabilities_array = []

    grams = create_ngrams(sentences, N, token_start_word, token_end_word)
    num_words = get_word_count_in_corpus(sentences)

    # if the oov word found, we add a small laplace calculated value for that oov
    laplace_value_for_oov = laplace_value / (number_unique_words * laplace_value)

    for grams_i in grams:

        p = lm_prob[tuple(grams_i[:-1])][grams_i[-1]]
        
        # means the word is oov, and having 0 probability. To handle oov, we will add small laplace calculated 
        if p == 0:
            lm_prob[tuple(grams_i[:-1])][grams_i[-1]] = laplace_value_for_oov
            p = laplace_value_for_oov
            count_oov += 1
        
        probabilities_array.append(p)
        
        log_probs += np.log(p)

    
    avg_log_prob = log_probs / num_words
    perplexity = np.exp(-avg_log_prob)
    variance = np.var(probabilities_array)
    
    return perplexity, count_oov, variance

### 1. Main driver function starts

In [12]:
file_path = r"C:\Users\tanmay.jain\Downloads\s2\Natural Language Processing\Assignment\Assignment1\eng_news_2020_10K-sentences-1.txt"

#### 1.1 Reading data from file, and pre-processing of the data. 

In [13]:
# reading file
raw_data = read_text_data_from_file(file_path)

# processing & clearing the train data
cleared_data = preprocessing_cleaning_data(raw_data)

#### 1.2 Split the data for training and testing.

In [14]:
#spliting data to train, test
train_data, test_data = split_data_into_train_test(cleared_data, training_size=0.90)

### 2. Experiment with bigram LM

In [15]:
# Setting the basic configuration of LM

N = 2 #number of ngram
token_start_word = "<s>"
token_end_word = "</s>"
laplace_value = 1

#### 2.1 Developing n-gram language model based on user N value

In [16]:
# Creating the ngrams, and ngram LM on the training dataset

unique_words, number_unique_words, unigram_freq = get_unique_words_count(train_data)
grams = create_ngrams(train_data, N, token_start_word, token_end_word)

#lm_prob contains the ngrams with probability values
lm_prob = create_lm_model(grams, number_unique_words, laplace_value)

In [17]:
# printing lm probabilities
lm_prob

defaultdict(<function __main__.create_lm_model.<locals>.<lambda>()>,
            {('<s>',): defaultdict(<function __main__.create_lm_model.<locals>.<lambda>.<locals>.<lambda>()>,
                         {'were': 0.0007261247040252565,
                          'westlake': 6.314127861089187e-05,
                          'he': 0.007861089187056037,
                          'we': 0.006692975532754538,
                          'the': 0.03895816890292028,
                          'now': 0.0012312549329123914,
                          'and': 0.00372533543804262,
                          'but': 0.006093133385951065,
                          'earlier': 0.00028413575374901343,
                          'officials': 0.00037884767166535124,
                          'this': 0.005998421468034728,
                          'however': 0.0021152328334648777,
                          'wisconsin': 6.314127861089187e-05,
                          's': 0.00015785319652722967,
                   

#### 2.2 Take a sentence and return the probability (after processing in log) assigned to that sentence by the model. 

In [18]:
'''
Here we're imaging that the input will be any random sentence from the training corpus. 
So, we're randomly taking any sentence, getting it's probability in log and displaying.

Since when we multiply the ngrams probabilities, the value will be underflow, to control that,
our function is returning the probability into log
'''
random_sentence_index = random.randint(0, len(train_data)-1)

prob = get_sentence_prob(train_data[random_sentence_index], N, token_start_word, token_end_word, lm_prob)
print("Sentence: ",train_data[random_sentence_index], " \n\n Probability (processed in log): ", prob)

Sentence:  he went on to cite achievements in the area of regional integration noting that on 3 december 2019 burundi democratic republic of the congo and the united republic of tanzania agreed to build a railway to boost trade  

 Probability (processed in log):  -322.5746832465941


#### 2.2 Implementation sentence generation

In [19]:
text_data = ["and"]
number_of_time_sentence_generate = 10
generated_sentences = generate_random_sentences(text_data, number_of_time_sentence_generate, N)

for i in generated_sentences:
    print(i)

('and stirring as we didnt create a host galaxy coming weeks it is just thunder cutting </s>', 9.468025676840052e-61)
('and walks while vince wilfork donta hightower devin mccourty and pigments are assets it refers to treat a moron for schools center for once valued at the company for nearly one person to companies with our latest of both world a difference between july belta on strong company for almost 1000 m respectively </s>', 1.1699002227947956e-207)
('and fun </s>', 1.618317214691585e-08)
('and fort st </s>', 8.555738167391516e-13)
('and capital of the mum </s>', 1.4138224893475686e-18)
('and critical services department of the standard heel logic to labor department must prepare a jack britt </s>', 6.727875724163854e-66)
('and selfishness cold chain and surrounding water she died after covid19 is open for getting out of their condition of fresh lockdown does anyone who died mai ashlee had there will also expressed concern over the same day signify malintent of tomorrow </s>', 2.

#### 2.3 Getting the perplexity, variance of the LM, and handling OOV in the text corpus

In [20]:
perplexity, count_oov, variance = get_perplexity_variance(test_data, N, token_start_word, token_end_word, lm_prob, laplace_value, number_unique_words)

print("Perplexity:- ", perplexity)
print("Number of OOV Found:- ", count_oov)
print("Variance: - ", variance)

Perplexity:-  10967.310825848304
Number of OOV Found:-  10050
Variance: -  3.0301105181114896e-05


### 3. Experiment with trigram LM

In [21]:
#Setting the basic configuration of LM

N = 3 #number of ngram
token_start_word = "<s>"
token_end_word = "</s>"
laplace_value = 1

#### 3.1 Developing n-gram language model based on user N value

In [22]:
# Creating the ngrams, and ngram LM on the training dataset

unique_words, number_unique_words, unigram_freq = get_unique_words_count(train_data)
grams = create_ngrams(train_data, N, token_start_word, token_end_word)

#lm_prob contains the ngrams with probability values
lm_prob = create_lm_model(grams, number_unique_words, laplace_value)

In [23]:
# printing lm probabilities
lm_prob

defaultdict(<function __main__.create_lm_model.<locals>.<lambda>()>,
            {('<s>',
              '<s>'): defaultdict(<function __main__.create_lm_model.<locals>.<lambda>.<locals>.<lambda>()>,
                         {'were': 0.0007261247040252565,
                          'westlake': 6.314127861089187e-05,
                          'he': 0.007861089187056037,
                          'we': 0.006692975532754538,
                          'the': 0.03895816890292028,
                          'now': 0.0012312549329123914,
                          'and': 0.00372533543804262,
                          'but': 0.006093133385951065,
                          'earlier': 0.00028413575374901343,
                          'officials': 0.00037884767166535124,
                          'this': 0.005998421468034728,
                          'however': 0.0021152328334648777,
                          'wisconsin': 6.314127861089187e-05,
                          's': 0.00015785319652722967,

#### 3.2 Take a sentence and return the probability (after processing in log) assigned to that sentence by the model. 

In [24]:
'''
Here we're imaging that the input will be any random sentence from the training corpus. 
So, we're randomly taking any sentence, getting it's probability in log and displaying.

Since when we multiply the ngrams probabilities, the value will be underflow, to control that,
our function is returning the probability into log
'''
random_sentence_index = random.randint(0, len(train_data)-1)

prob = get_sentence_prob(train_data[random_sentence_index], N, token_start_word, token_end_word, lm_prob)
print("Sentence: ",train_data[random_sentence_index], " \n\n Probability (processed in log): ", prob)

Sentence:  pge spokesman james noonan said were disappointed with the proposed decision saying that pge worked diligently over many months with multiple parties to reach the previous settlement  

 Probability (processed in log):  -270.2775151705175


#### 3.3 Implementation sentence generation
 

In [25]:
text_data = ["and","some"]
number_of_time_sentence_generate = 10
generated_sentences = generate_random_sentences(text_data, number_of_time_sentence_generate, N)

for i in generated_sentences:
    print(i)

('and some of the documents now helping to set up the sleeve </s>', 3.1099901097695522e-43)
('and some of the shelters are located and that reporters are more than 180mph while sensors study the impact of its classes remotely except for down there were holes in the care of black america series </s>', 2.181627366644283e-140)
('and some negative impacts to usborn employment rates in its documented advice to contain this pandemic due to the worksites and also embroiderers will absolutely fall for the coal states and labuan </s>', 2.1483834582386906e-125)
('and some who will be crowdfunded </s>', 7.923707201507366e-21)
('and some of the elements leave a comment directly on another device </s>', 1.0384928354514115e-43)
('and some education programs a child </s>', 8.000585351763054e-21)
('and some of the matric exams during the golden state warriors basketball game </s>', 6.078657562602922e-48)
('and some of the spectacular dept of speculation we learned that the second edition in a monthly 

#### 3.4 Getting the perplexity, variance of the LM, and handling OOV in the text corpus

In [26]:
perplexity, count_oov, variance = get_perplexity_variance(test_data, N, token_start_word, token_end_word, lm_prob, laplace_value, number_unique_words)

print("Perplexity:- ", perplexity)
print("Number of OOV Found:- ", count_oov)
print("Variance: - ", variance)

Perplexity:-  41752.68847138416
Number of OOV Found:-  17131
Variance: -  1.1246018075344019e-05


### Justification

Perplexity depends on various factors, including the quality and size of the training data, the complexity of the language being modelled, and the effectiveness of the language model itself.
A lower perplexity indicates that the language model performs better in terms of predicting the next word in a sequence of words. 
In general, a bigram model tends to have higher perplexity compared to higher-order n-gram models (such as trigram, 4-gram, etc.). However, bigram can have lower perplexity as compared to higher n-gram model due to data size, quality and data characteristics.

With the provided dataset, we are getting below results:
### Output for bigram model:

Perplexity:-  10967.310825848304

Number of OOV Found:-  10,050

Variance: -  3.0301105181114896e-05

### Output for trigram model:

Perplexity:-  41752.68847138416

Number of OOV Found:-  17,131

Variance: -  1.1246018075344019e-05


Here we can see perplexity of bigram is less as compared to trigram. Hence here a bigram model is performing better for the provided data set. 
 

